In [1]:
from splinter import Browser
from bs4 import BeautifulSoup as bs
from webdriver_manager.chrome import ChromeDriverManager
import pandas as pd 
import time
import csv 

In [2]:
#NASA Mars News 
executable_path = {'executable_path': ChromeDriverManager().install()}

#swithced headless to True so the window doesnt popup
browser = Browser('chrome', **executable_path, headless=False)

[WDM] - ====== WebDriver manager ======
[WDM] - Current google-chrome version is 104.0.5112
[WDM] - Get LATEST chromedriver version for 104.0.5112 google-chrome
[WDM] - Driver [C:\Users\bfo2f\.wdm\drivers\chromedriver\win32\104.0.5112.79\chromedriver.exe] found in cache


In [3]:
# Visit the following URL
url = "https://bringatrailer.com/auctions/results/"
browser.visit(url)
# it was going to fast and was saing there was no index so it wasnt scraping anything, very fusterating error. adding a time delay helped.

In [4]:
html = browser.html
soup = bs(html, 'html.parser')


In [5]:
for i in range(2000):
    browser.find_by_xpath('/html/body/main/div[6]/div/div/div/div[2]/div[5]/button').click()
    time.sleep(.5)
    #If error return continue

ElementDoesNotExist: no elements could be found with xpath "/html/body/main/div[6]/div/div/div/div[2]/div[5]/button"

In [5]:
# results = soup.find_all('div', class_='block')[0]
#results = soup.find_all('div', class_='block')
#results

In [6]:
HTMLFileToBeOpened = open("Auction Results _ Bring a Trailer.html", "r", encoding='utf-8')
  
# Reading the file and storing in a variable
contents = HTMLFileToBeOpened.read()
  
beautifulSoupText = bs(contents, 'lxml')
results = beautifulSoupText.find_all('div', class_='block')
results

[<div class="block">
 <a data-bind="attr: { href: url }" href="https://bringatrailer.com/listing/1999-porsche-911-carrera-297/">
 <img alt="44k-Mile 1999 Porsche 911 Carrera Coupe 6-Speed" data-bind="attr: { src: images.small.url, height: images.small.height, width: images.small.width, alt: title }" height="150" src="./Auction Results _ Bring a Trailer_files/1999_porsche_911-carrera_5v0b7070-99316.jpg" width="150"/>
 </a>
 <h3 class="title"><a data-bind="attr: { href: url }, text: title" href="https://bringatrailer.com/listing/1999-porsche-911-carrera-297/">44k-Mile 1999 Porsche 911 Carrera Coupe 6-Speed</a></h3>
 <div class="subtitle" data-bind="text: subtitle">Sold for $29,840 on 8/25/22</div>
 </div>,
 <div class="block">
 <a data-bind="attr: { href: url }" href="https://bringatrailer.com/listing/1976-triumph-tr6-128/">
 <img alt="1976 Triumph TR6" data-bind="attr: { src: images.small.url, height: images.small.height, width: images.small.width, alt: title }" height="150" src="./Auct

In [7]:
title_list = []
year_list = []
make_list = []
model_list = []
price_list = []
mileage_list = []
engine_list = []
zip_list = []
cf_list = []

for i in results:
    image_click = i.find('a')['href']
    image_click
    try:
        browser.visit(image_click)

        time.sleep(.1)

        html = browser.html
        soup = bs(html, 'html.parser')
    
    
        
        try: 
            year = soup.find('h1', class_='post-title').get_text()
            year = year.split()
            for word in year:
                try:
                    j = int(word)
                    if j > 1900:
                        if j < 2023:
                            car_year = j
                except:
                    pass
        except: 
            car_year = ""
    
        try:
            make_model = soup.find('div', class_='column-groups')
            make_model = make_model.find_all('button')
            make_pre = make_model[0].get_text()
            if make_pre[:4].lower() == 'make':
                make = make_pre[4:]
            else:
                make = ''
            model_pre = make_model[1].get_text()
            if model_pre[:5].lower() == 'model':
                model = model_pre[5:]
            else: model = ''
        
        except:
            make = ''
            model = ''
    
        try:
            price = soup.find('span', class_='info-value')
            price = price.find('strong').get_text()
        except:
            price = 0

        try:
            aList = soup.find('div', class_='essentials')
            bList = aList.find_all('li')
            bList_text = bList[1].get_text()
            mile_list = []
            for char in bList_text:
                if char.isnumeric():
                    mile_list.append(int(char))
            mile_list.reverse()
            multiplier = 1000
            mileage = 0
            for num in mile_list:
                mileage = mileage + num * multiplier
                multiplier = multiplier * 10
            if mileage > 1000000:
                mileage = 0
            engine = bList[2].get_text()
            carfax = bList[-1].get_text()
        except:
            mileage = 0
            engine = ''

        try:
            div = soup.find('div', class_='essentials')
            location = div.find_all('a')
            location = location[2].get_text()
            location = location.split()
            for word in location:
                try:
                    zipcode = int(word)
                except:
                    pass
        except:
            zipcode = 0
        
        year_list.append(car_year)
        make_list.append(make)
        model_list.append(model)
        price_list.append(price)
        mileage_list.append(mileage)
        engine_list.append(engine)
        zip_list.append(zipcode)
        cf_list.append(carfax)
        
        df1 = pd.DataFrame({
    
        "year": year_list, 
        'make': make_list,
        'model': model_list,
        "final_price": price_list,
        'mileage': mileage_list,
        'engine': engine_list,
        'zipcode': zip_list,
        'car_fax_report': cf_list
    
        })

        print(df1)
    except:
        pass
    

    

    
#     print(title)

df1 = pd.DataFrame({
    
    "year": year_list, 
    'make': make_list,
    'model': model_list,
    "final_price": price_list,
    'mileage': mileage_list,
    'engine': engine_list,
    'zipcode': zip_list,
    'car_fax_report': cf_list
    
})

df1

   year     make            model final_price  mileage              engine  \
0  1999  Porsche  Porsche 996 911     $29,840    44000  3.4-Liter Flat-Six   

   zipcode         car_fax_report  
0    33407  Recent Service Record  
   year     make            model final_price  mileage                engine  \
0  1999  Porsche  Porsche 996 911     $29,840    44000    3.4-Liter Flat-Six   
1  1976  Triumph      Triumph TR6     $23,500    95000  2.5-Liter Inline-Six   

   zipcode         car_fax_report  
0    33407  Recent Service Record  
1    46229        Service Manuals  
   year       make                  model final_price  mileage  \
0  1999    Porsche        Porsche 996 911     $29,840    44000   
1  1976    Triumph            Triumph TR6     $23,500    95000   
2  2015  Chevrolet  Chevrolet Corvette C7     $87,000   410000   

                      engine  zipcode               car_fax_report  
0         3.4-Liter Flat-Six    33407        Recent Service Record  
1       2.5-Liter I

In [ ]:
df = pd.DataFrame({
    
    "year": year_list, 
    'make': make_list,
    'model': model_list,
    "final_price": price_list,
    'mileage': mileage_list,
    'engine': engine_list,
    'zipcode': zip_list,
    'car_fax_report': cf_list
    
})
df.head(20)

In [ ]:
df

year        make                                      model final_price  \
0    1993  Land Rover  Land Rover 110 / Defender 110 (Euro Spec)     $59,500   
1    1997   Chevrolet                         Chevrolet Suburban     $17,000   
2    1990     Porsche                            Porsche 964 911    $225,000   
3    2003      Toyota                              Toyota Pickup     $24,750   
4    1971     Triumph                                Triumph TR6     $15,250   
..    ...         ...                                        ...         ...   
328  2004         BMW                                 BMW E46 M3     $19,000   
329  1982   Chevrolet                      Chevrolet Corvette C3     $24,250   
330  2021        Jeep                                Jeep Pickup     $70,005   
331  1965       Honda                          Honda Motorcycles     $12,000   
332  2002         GMC                           GMC Yukon GMT800     $31,250   

     mileage                                    engine  zipcode  
0          0  2.5-Liter 200Tdi Turbodiesel Inline-Four    20895  
1      67000                            5.7L Vortec V8    60069  
2       1000                       3.8-Liter Flat-Six     84790  
3     116000                         3.4-Liter DOHC V6    90027  
4          0                      32k Miles Shown, TMU    28724  
..       ...                                       ...      ...  
328        0                  3.2-Liter S54 Inline-Six     7849  
329        0                              5.7-Liter V8     7728  
330     6000                 Replacement 392ci Hemi V8    92003  
331    11000           305cc Four-Stroke Parallel Twin    65233  
332    47000                              5.3-Liter V8    15747  

[333 rows x 7 columns]

In [ ]:
df.to_csv('dataset1.csv', mode='a')